In [18]:
import lzma
import torch
import numpy as np
from gensim import downloader
from gensim.models import Word2Vec
import gensim.downloader
import pandas as pd
import csv

In [19]:
from sklearn.model_selection import train_test_split

from sklearn.datasets import fetch_20newsgroups
# https://scikit-learn.org/0.19/datasets/twenty_newsgroups.html

from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics import accuracy_score

In [4]:
train_x = pd.read_csv('train/in.tsv', header=None, sep='\t', quoting=csv.QUOTE_NONE, error_bad_lines=False)
train_y = pd.read_csv('train/expected.tsv', header=None, sep='\t', quoting=csv.QUOTE_NONE, error_bad_lines=False)
dev_x = pd.read_csv('dev-0/in.tsv', header=None, sep='\t', quoting=csv.QUOTE_NONE, error_bad_lines=False)
dev_y = pd.read_csv('dev-0/expected.tsv', header=None, sep='\t', quoting=csv.QUOTE_NONE, error_bad_lines=False)
test_x = pd.read_csv('test-A/in.tsv', header=None, sep='\t',quoting=csv.QUOTE_NONE, error_bad_lines=False)

C:\Users\10118794\AppData\Local\Temp\ipykernel_32100\3675615398.py:1: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  train_x = pd.read_csv('train/in.tsv', header=None, sep='\t', quoting=csv.QUOTE_NONE, error_bad_lines=False)
C:\Users\10118794\AppData\Local\Temp\ipykernel_32100\3675615398.py:2: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  train_y = pd.read_csv('train/expected.tsv', header=None, sep='\t', quoting=csv.QUOTE_NONE, error_bad_lines=False)
C:\Users\10118794\AppData\Local\Temp\ipykernel_32100\3675615398.py:3: FutureWarning: The error_bad_lines argument has been deprecated and will be removed in a future version. Use on_bad_lines in the future.


  dev_x = pd.read_csv('dev-0/in.tsv', header=None, sep='\t', quoting=csv.QUOTE_NONE, error_bad_lines=False)
C:\Users\10118794\AppData\Local\Temp\ip

In [5]:
train_x = train_x[0]
dev_x = dev_x[0]
test_x = test_x[0]
train_y = train_y[0]
dev_y = dev_y[0]
train_y = train_y.to_numpy()
dev_y = dev_y.to_numpy()

In [83]:
word2vec_100 = downloader.load("glove-twitter-100")

[==================================================] 100.0% 387.1/387.1MB downloaded


In [105]:
train_x_w2v = [np.mean([word2vec_100[word.lower()] for word in doc.split() if word.lower() in word2vec_100]
                   or [np.zeros(100, dtype=float)], axis=0) for doc in train_x]


In [106]:
dev_x_w2v2 = [np.mean([word2vec_100[word.lower()] for word in doc.split() if word.lower() in word2vec_100]
                   or [np.zeros(100, dtype=float)], axis=0) for doc in dev_x]

In [108]:
test_x_w2v = [np.mean([word2vec_100[word.lower()] for word in doc.split() if word.lower() in word2vec_100]
                   or [np.zeros(100, dtype=float)], axis=0) for doc in test_x]

In [56]:
print(type(x_train_w2v))

<class 'list'>


In [78]:
class NeuralNetworkModelx(torch.nn.Module):

    def __init__(self):
        super(NeuralNetworkModelx, self).__init__()
        self.fc1 = torch.nn.Linear(100,500)
        self.fc2 = torch.nn.Linear(500,1)

    def forward(self, x):
        x = self.fc1(x)
        x = torch.relu(x)
        x = self.fc2(x)
        x = torch.sigmoid(x)
        return x

In [71]:
def predict(model, data):
    model.eval()
    predictions = []
    for x in data:
        X = torch.tensor(np.array(x).astype(np.float32))
        Y_predictions = model(X)
        if Y_predictions[0] > 0.5:
            predictions.append("1")
        else:
            predictions.append("0")
    return predictions

In [93]:
BATCH_SIZE = 22

In [94]:
FEATURES = 100

In [95]:
model = NeuralNetworkModelx()
criterion = torch.nn.BCELoss()
optimizer = torch.optim.ASGD(model.parameters(), lr=0.1)

In [97]:
def get_loss_acc(model, X_dataset, Y_dataset):
    loss_score = 0
    acc_score = 0
    items_total = 0
    model.eval()
    for i in range(0, Y_dataset.shape[0], BATCH_SIZE):
        X = np.array(X_dataset[i:i+BATCH_SIZE]).astype(np.float32)
        X = torch.tensor(X)
        Y = Y_dataset[i:i+BATCH_SIZE]
        Y = torch.tensor(Y.astype(np.float32)).reshape(-1,1)
        Y_predictions = model(X)
        acc_score += torch.sum((Y_predictions > 0.5) == Y).item()
        items_total += Y.shape[0]

        loss = criterion(Y_predictions, Y)

        loss_score += loss.item() * Y.shape[0]

In [107]:
for epoch in range(10):
    loss_score = 0
    acc_score = 0
    items_total = 0
    for i in range(0, train_y.shape[0], BATCH_SIZE):
        x = train_x_w2v[i:i+BATCH_SIZE]
        x = torch.tensor(np.array(x).astype(np.float32))
        y = train_y[i:i+BATCH_SIZE]
        y = torch.tensor(y.astype(np.float32)).reshape(-1, 1)
        y_pred = model(x)
        acc_score += torch.sum((y_pred > 0.5) == y).item()
        items_total += y.shape[0]

        optimizer.zero_grad()
        loss = criterion(y_pred, y)
        loss.backward()
        optimizer.step()

        loss_score += loss.item() * y.shape[0]
    display(epoch)
    #display(get_loss_acc(model, train_x_w2v, train_y))
    #display(get_loss_acc(model, dev_x_w2v2, dev_y))
    print((loss_score / items_total), (acc_score / items_total))

0

0.5251316127311283 0.7293691876828085


1

0.5236849654193508 0.7303671882284282


2

...

0.5173362161154499 0.7348944502191112


8

0.5163200458762819 0.7358717310302197


9

0.5155178654158614 0.7361583540242904


In [119]:
pred_dev = predict(model, dev_x_w2v2)
pred_test = predict(model, test_x_w2v)

In [120]:
dev_pred = [int(i) for i in pred_dev]
test_pred = [int(i) for i in pred_test]

In [121]:
dev_pred = np.array(dev_pred)
test_pred = np.array(test_pred)

In [122]:
type(dev_pred)

numpy.ndarray

In [123]:
dev_pred

array([0, 1, 0, ..., 0, 1, 0])

In [124]:
np.savetxt("dev-0/out.tsv",dev_pred, delimiter="\t", fmt='%d')
np.savetxt("test-A/out.tsv",test_pred, delimiter="\t", fmt='%d')